In [35]:
import numpy as np
import math
class Node:
    def __init__(self,numtheta):
        self.theta=[0.0]*numtheta
        self.downstream=None
        self.upstream=None
        self.output=None
        self.deljthetabydelthetaunit = [0.0]*numtheta
        self.deljthetabydelnet = None
def loadtheta(network,theta ):
    for i in range(len(network)):
        for j in range(len(network[i])):
            for k in range(len(network[i][j].theta)):
                network[i][j].theta[k] = theta[i][j][k]
    return network
def sigmoid(x):
    return (1.0/(1.0+math.exp(-x)))
def forwardpass(features, network):
    for i in range(len(network)):
        for j in range(len(network[i])):
            tempnode = network[i][j]
            temp=0.0
            if(i==0):
                #parse from input
                for k in range(len(tempnode.theta)):
                    if(k==len(tempnode.theta)-1):
                        temp += tempnode.theta[k] * 1.0
                    else:
                        temp += tempnode.theta[k] * features[k]
                
            else:
                #parse from last layer
                prevlayer = network[i-1]
                for k in range(len(tempnode.theta)):
                    if(k==len(tempnode.theta)-1):
                        temp += tempnode.theta[k] * 1.0
                    else:
                        temp += tempnode.theta[k] * prevlayer[k].output
            tempnode.output = sigmoid(temp)
    lastlayer = network[len(network)-1]
    templist=[]
    for i in range(len(lastlayer)):
        templist.append(lastlayer[i].output)
    return templist
def findcost(output, correctoutput):
    temp = 0.0
    for i in range(len(output)):
        temp += 0.5 * ((output[i]-correctoutput[i])**2)
    return temp
def findtotalcostarr(inparr,outarr,network):
    costarr=[]
    for i in range(len(inparr)):
        tempforwardpass= forwardpass(inparr[i],network)
        print("tempforwardpass is")
        print(tempforwardpass)
        tempcost = findcost(tempforwardpass,outarr[i])
        costarr.append(tempcost)
    avgcost=0.0
    for i in range(len(costarr)):
        avgcost += costarr[i]
    avgcost = avgcost/(len(costarr))
    return costarr, avgcost
def printdeljtheta(network):
    print("deljtheta is")
    templist=[]
    for i in range(len(network)):
        templist.append([])
        for j in range(len(network[i])):
            templist[i].append([])
            for k in range(len(network[i][j].theta)):
                templist[i][j].append(network[i][j].deljthetabydelthetaunit[k])
    print(templist)
    return
def neuralnet(inparr, outarr, hiddeninfo,learningrate, epochsize,costthres, sampletheta):
    numtrain = len(inparr)
    diminput= len(inparr[0])
    dimoutput = len(outarr[0])
    network=[]
    for i in range(len(hiddeninfo)):
        network.append([])
    network.append([])
    for i in range(len(hiddeninfo)):
        #i is layer iterator
        for j in range(hiddeninfo[i]):
            #j is sublayer num unit iterator
            if(i==0):
                tempnode = Node(diminput+1)
                network[i].append(tempnode)
            else:
                tempnode = Node(hiddeninfo[i-1]+1)
                network[i].append(tempnode)
            
    #add output layer
    for i in range(dimoutput):
        tempnode = Node(hiddeninfo[len(hiddeninfo)-1] + 1)
        network[len(network)-1].append(tempnode)
    #load theta for testing
#     network = loadtheta(network, sampletheta)
    #necessary forwardpass
#     tempforwardpass = forwardpass(inparr[0],network)
#     print(tempforwardpass)
#     #lets see cost
#     print("cost = "+str(findcost(tempforwardpass,outarr[0])))
    
    #time for backprop
    deljthetabydelthetamat=[]
    for i in range(len(network)):
        deljthetabydelthetamat.append([])
        for j in range(len(network[i])):
            deljthetabydelthetamat[i].append([])
            for k in range(len(network[i][j].theta)):
                deljthetabydelthetamat[i][j].append(0.0)
    print("simulated deljtheata")
    print(deljthetabydelthetamat)
    print("real deljtheta")
    printdeljtheta(network)
    subepochiter=0
    epochcount=0
    numwholedatapass=0
    numiter=0
    costarr,oldavgcost = findtotalcostarr(inparr,outarr,network)
    
    while(0==0):
        numiter+=1
        print("numiter is")
        print(numiter)
        print("numwholedata pass is")
        print(numwholedatapass)
        ioindex = epochsize*epochcount+subepochiter
        print("ioindex is "+str(ioindex))
        tempforwardpass = forwardpass(inparr[ioindex],network)
        for i in range(len(network)-1,-1,-1):
            #lets calculate deljtheta by del netj
            for j in range(len(network[i])):
                tempnode = network[i][j]
                if(i==len(network)-1):
                    tempnode.deljthetabydelnet = -1.0*(outarr[ioindex][j]-tempnode.output)*(tempnode.output)*(1.0-tempnode.output)
                else:
                    temp=0.0
                    nextlayer = network[i+1]
                    for k in range(len(nextlayer)):
                        temp += nextlayer[k].deljthetabydelnet * nextlayer[k].theta[j]
                    tempnode.deljthetabydelnet = (tempnode.output) * (1.0- tempnode.output) * temp
                if(i==0):
                    #ok is input
                    for k in range(len(tempnode.theta)):
                        if(k==len(tempnode.theta)-1):
                            tempnode.deljthetabydelthetaunit[k] = tempnode.deljthetabydelnet * 1.0
                        else:
                            tempnode.deljthetabydelthetaunit[k] = tempnode.deljthetabydelnet * inparr[ioindex][k]
                else:
                    prevlayer = network[i-1]
                    for k in range(len(tempnode.theta)):
                        if(k==len(tempnode.theta)-1):
                            tempnode.deljthetabydelthetaunit[k] = tempnode.deljthetabydelnet * 1.0
                        else:
                            tempnode.deljthetabydelthetaunit[k] = tempnode.deljthetabydelnet * prevlayer[k].output
        subepochiter+=1
        for i in range(len(network)):
                for j in range(len(network[i])):
                    for k in range(len(network[i][j].theta)):
                        deljthetabydelthetamat[i][j][k] += network[i][j].deljthetabydelthetaunit[k]
        print("simulated deljtheata")
        print(deljthetabydelthetamat)
        print("real deljtheta")
        printdeljtheta(network)
        if(subepochiter==epochsize):
            print("epoch over")
            for i in range(len(network)):
                for j in range(len(network[i])):
                    for k in range(len(network[i][j].theta)):
                        network[i][j].theta[k] = network[i][j].theta[k] - learningrate * deljthetabydelthetamat[i][j][k]/(1.0*epochsize)
                        deljthetabydelthetamat[i][j][k]=0.0
            #set deljthetabydel zero
            
            costarr, newavgcost=findtotalcostarr(inparr,outarr,network)
            print("cost is")
            print(newavgcost)
            if(newavgcost<costthres):
                print("cost is lower")
                break
            elif(numwholedatapass>=2000):
                break
            else:
                oldavgcost=newavgcost
                subepochiter=0
                epochcount+=1
                if(len(inparr)==epochcount*epochsize):
                    numwholedatapass+=1
                    epochcount=0
        
            
            
            
#         tempforwardpass = forwardpass(inparr[0],network)
#         print(tempforwardpass)
#         #lets see cost
#         print("cost = "+str(findcost(tempforwardpass,outarr[0])))        
    
    return network
# sampleinparr = [[0.05, 0.10]]
sampleinparr = [[0.0, 1.0],[1.0,0.0],[0.0,0.0],[1.0,1.0]]

# sampleoutput = [[0.01, 0.99]]
sampleoutput = [[1.0],[1.0],[0.0],[1.0]]
samplehiddeninfo = [2]
samplelearningrate=0.5
sampletheta = [[[.15,.20,.35],[.25,.30,.35]],[[.40,.45,.60],[.50,.55,.60]]]

samplenetwork = neuralnet(sampleinparr,sampleoutput,samplehiddeninfo,samplelearningrate,1, pow(10,-5),sampletheta)
print(samplenetwork)
            
                
    
    

simulated deljtheata
[[[0.0, 0.0, 0.0], [0.0, 0.0, 0.0]], [[0.0, 0.0, 0.0]]]
real deljtheta
deljtheta is
[[[0.0, 0.0, 0.0], [0.0, 0.0, 0.0]], [[0.0, 0.0, 0.0]]]
tempforwardpass is
[0.5]
tempforwardpass is
[0.5]
tempforwardpass is
[0.5]
tempforwardpass is
[0.5]
numiter is
1
numwholedata pass is
0
ioindex is 0
simulated deljtheata
[[[0.0, 0.0, 0.0], [0.0, 0.0, 0.0]], [[-0.0625, -0.0625, -0.125]]]
real deljtheta
deljtheta is
[[[0.0, 0.0, 0.0], [0.0, 0.0, 0.0]], [[-0.0625, -0.0625, -0.125]]]
epoch over
tempforwardpass is
[0.523420348936324]
tempforwardpass is
[0.523420348936324]
tempforwardpass is
[0.523420348936324]
tempforwardpass is
[0.523420348936324]
cost is
0.11941916913806858
numiter is
2
numwholedata pass is
0
ioindex is 1
simulated deljtheata
[[[-0.0009287773652627883, 0.0, -0.0009287773652627883], [-0.0009287773652627883, 0.0, -0.0009287773652627883]], [[-0.05944175137681845, -0.05944175137681845, -0.1188835027536369]]]
real deljtheta
deljtheta is
[[[-0.0009287773652627883, -0.0,

numwholedata pass is
20
ioindex is 1
simulated deljtheata
[[[-0.004386223461014114, 0.0, -0.004386223461014114], [-0.004386223461014114, 0.0, -0.004386223461014114]], [[-0.0249733940355654, -0.0249733940355654, -0.04760046299359557]]]
real deljtheta
deljtheta is
[[[-0.004386223461014114, -0.0, -0.004386223461014114], [-0.004386223461014114, -0.0, -0.004386223461014114]], [[-0.0249733940355654, -0.0249733940355654, -0.04760046299359557]]]
epoch over
tempforwardpass is
[0.7546893687468988]
tempforwardpass is
[0.7547354122929609]
tempforwardpass is
[0.7518368510849194]
tempforwardpass is
[0.7575535981300454]
cost is
0.0930463665272342
numiter is
83
numwholedata pass is
20
ioindex is 2
simulated deljtheata
[[[0.0, 0.0, 0.013393859428533529], [0.0, 0.0, 0.013393859428533529]], [[0.07088497579840894, 0.07088497579840894, 0.1402763666966166]]]
real deljtheta
deljtheta is
[[[0.0, 0.0, 0.013393859428533529], [0.0, 0.0, 0.013393859428533529]], [[0.07088497579840894, 0.07088497579840894, 0.140276

tempforwardpass is
[0.761620952196707]
tempforwardpass is
[0.7615611973226638]
tempforwardpass is
[0.7554591522028692]
tempforwardpass is
[0.7675359918382993]
cost is
0.09230445984893593
numiter is
154
numwholedata pass is
38
ioindex is 1
simulated deljtheata
[[[-0.004520988609869714, 0.0, -0.004520988609869714], [-0.004520988609869714, 0.0, -0.004520988609869714]], [[-0.023485967013753214, -0.023485967013753214, -0.043297086442024284]]]
real deljtheta
deljtheta is
[[[-0.004520988609869714, -0.0, -0.004520988609869714], [-0.004520988609869714, -0.0, -0.004520988609869714]], [[-0.023485967013753214, -0.023485967013753214, -0.043297086442024284]]]
epoch over
tempforwardpass is
[0.7678961293980061]
tempforwardpass is
[0.767922308167914]
tempforwardpass is
[0.7616760433227103]
tempforwardpass is
[0.7739438018913152]
cost is
0.0923730076837035
numiter is
155
numwholedata pass is
38
ioindex is 2
simulated deljtheata
[[[0.0, 0.0, 0.01494717172812845], [0.0, 0.0, 0.01494717172812845]], [[0.069

numwholedata pass is
50
ioindex is 0
simulated deljtheata
[[[0.0, -0.004861034451588, -0.004861034451588], [0.0, -0.004861034451588, -0.004861034451588]], [[-0.024705245399581854, -0.024705245399581854, -0.0446821593307855]]]
real deljtheta
deljtheta is
[[[-0.0, -0.004861034451588, -0.004861034451588], [-0.0, -0.004861034451588, -0.004861034451588]], [[-0.024705245399581854, -0.024705245399581854, -0.0446821593307855]]]
epoch over
tempforwardpass is
[0.7638141429724384]
tempforwardpass is
[0.7637246059228329]
tempforwardpass is
[0.7549386833247144]
tempforwardpass is
[0.7721845023308284]
cost is
0.09168026718305876
numiter is
202
numwholedata pass is
50
ioindex is 1
simulated deljtheata
[[[-0.004767251629768577, 0.0, -0.004767251629768577], [-0.004767251629768577, 0.0, -0.004767251629768577]], [[-0.023601594572574294, -0.023601594572574294, -0.042635737083804914]]]
real deljtheta
deljtheta is
[[[-0.004767251629768577, -0.0, -0.004767251629768577], [-0.004767251629768577, -0.0, -0.00476

tempforwardpass is
[0.7459690667780767]
tempforwardpass is
[0.769181656832165]
cost is
0.0908637045206115
numiter is
249
numwholedata pass is
62
ioindex is 0
simulated deljtheata
[[[0.0, -0.005215446212321949, -0.005215446212321949], [0.0, -0.005215446212321949, -0.005215446212321949]], [[-0.02504194597700185, -0.02504194597700185, -0.04439989841376631]]]
real deljtheta
deljtheta is
[[[-0.0, -0.005215446212321949, -0.005215446212321949], [-0.0, -0.005215446212321949, -0.005215446212321949]], [[-0.02504194597700185, -0.02504194597700185, -0.04439989841376631]]]
epoch over
tempforwardpass is
[0.7648000054305806]
tempforwardpass is
[0.764669600448469]
tempforwardpass is
[0.7525956118742004]
tempforwardpass is
[0.7760579918144476]
cost is
0.09090620155512728
numiter is
250
numwholedata pass is
62
ioindex is 1
simulated deljtheata
[[[-0.005103322455663656, 0.0, -0.005103322455663656], [-0.005103322455663656, 0.0, -0.005103322455663656]], [[-0.02390747612151427, -0.02390747612151427, -0.0423

...

0.0003813494016494458
numiter is
7651
numwholedata pass is
1912
ioindex is 2
simulated deljtheata
[[[0.0, 0.0, 0.0009954967808963372], [0.0, 0.0, 0.0009954967808963372]], [[0.00023343737046089815, 0.00023343737046089815, 0.0018158623391381133]]]
real deljtheta
deljtheta is
[[[0.0, 0.0, 0.0009954967808963372], [0.0, 0.0, 0.0009954967808963372]], [[0.00023343737046089815, 0.00023343737046089815, 0.0018158623391381133]]]
epoch over
tempforwardpass is
[0.9762204284443771]
tempforwardpass is
[0.9761364275425679]
tempforwardpass is
[0.04351101815654166]
tempforwardpass is
[0.9953830544084515]
cost is
0.00038118287517678996
numiter is
7652
numwholedata pass is
1912
ioindex is 3
simulated deljtheata
[[[-6.925293095643603e-07, -6.925293095643603e-07, -6.925293095643603e-07], [-6.925293095643603e-07, -6.925293095643603e-07, -6.925293095643603e-07]], [[-2.1075293723694015e-05, -2.1075293723694015e-05, -2.1217770921588882e-05]]]
real deljtheta
deljtheta is
[[[-6.925293095643603e-07, -6.92529309564

deljtheta is
[[[-0.00039008470296282593, -0.0, -0.00039008470296282593], [-0.00039008470296282593, -0.0, -0.00039008470296282593]], [[-0.00045161855695294035, -0.00045161855695294035, -0.0005482724162763702]]]
epoch over
tempforwardpass is
[0.9764126370655193]
tempforwardpass is
[0.9763300830693598]
tempforwardpass is
[0.043299041940727374]
tempforwardpass is
[0.995418707579852]
cost is
0.0003765529913662623
numiter is
7723
numwholedata pass is
1930
ioindex is 2
simulated deljtheata
[[[0.0, 0.0, 0.0009832048853654373], [0.0, 0.0, 0.0009832048853654373]], [[0.00023020546039111776, 0.00023020546039111776, 0.0017936296846328857]]]
real deljtheta
deljtheta is
[[[0.0, 0.0, 0.0009832048853654373], [0.0, 0.0, 0.0009832048853654373]], [[0.00023020546039111776, 0.00023020546039111776, 0.0017936296846328857]]]
epoch over
tempforwardpass is
[0.976371494614754]
tempforwardpass is
[0.9762887756811208]
tempforwardpass is
[0.04323838741316143]
tempforwardpass is
[0.9954134262593377]
cost is
0.0003763

[0.04300785969798838]
tempforwardpass is
[0.9954450759163616]
cost is
0.00037191781879450126
numiter is
7794
numwholedata pass is
1948
ioindex is 1
simulated deljtheata
[[[-0.000385311776433157, 0.0, -0.000385311776433157], [-0.000385311776433157, 0.0, -0.000385311776433157]], [[-0.0004461397936207295, -0.0004461397936207295, -0.0005414627203575043]]]
real deljtheta
deljtheta is
[[[-0.000385311776433157, -0.0, -0.000385311776433157], [-0.000385311776433157, -0.0, -0.000385311776433157]], [[-0.0004461397936207295, -0.0004461397936207295, -0.0005414627203575043]]]
epoch over
tempforwardpass is
[0.9765603165809197]
tempforwardpass is
[0.9764790069590595]
tempforwardpass is
[0.04303005219851056]
tempforwardpass is
[0.9954484248137297]
cost is
0.0003718697626626866
numiter is
7795
numwholedata pass is
1948
ioindex is 2
simulated deljtheata
[[[0.0, 0.0, 0.0009711973460280796], [0.0, 0.0, 0.0009711973460280796]], [[0.00022705379632331302, 0.00022705379632331302, 0.0017719115761298963]]]
real 

ioindex is 0
simulated deljtheata
[[[0.0, -0.00037815055839300745, -0.00037815055839300745], [0.0, -0.00037815055839300745, -0.00037815055839300745]], [[-0.0004387389029921991, -0.0004387389029921991, -0.0005321134623084758]]]
real deljtheta
deljtheta is
[[[-0.0, -0.00037815055839300745, -0.00037815055839300745], [-0.0, -0.00037815055839300745, -0.00037815055839300745]], [[-0.0004387389029921991, -0.0004387389029921991, -0.0005321134623084758]]]
epoch over
tempforwardpass is
[0.9766849403788104]
tempforwardpass is
[0.9765985776827485]
tempforwardpass is
[0.0427439115067563]
tempforwardpass is
[0.9954743195575753]
cost is
0.0003673427907467929
numiter is
7866
numwholedata pass is
1966
ioindex is 1
simulated deljtheata
[[[-0.0003806482736033216, 0.0, -0.0003806482736033216], [-0.0003806482736033216, 0.0, -0.0003806482736033216]], [[-0.00044078651132967335, -0.00044078651132967335, -0.0005348113259162377]]]
real deljtheta
deljtheta is
[[[-0.0003806482736033216, -0.0, -0.000380648273603321

[0.9768018941452168]
tempforwardpass is
[0.9767227635739095]
tempforwardpass is
[0.04246319514386611]
tempforwardpass is
[0.9954998277472508]
cost is
0.0003629195428770386
numiter is
7937
numwholedata pass is
1984
ioindex is 0
simulated deljtheata
[[[0.0, -0.0003736417695280578, -0.0003736417695280578], [0.0, -0.0003736417695280578, -0.0003736417695280578]], [[-0.00043354612363482806, -0.00043354612363482806, -0.0005256680055141886]]]
real deljtheta
deljtheta is
[[[-0.0, -0.0003736417695280578, -0.0003736417695280578], [-0.0, -0.0003736417695280578, -0.0003736417695280578]], [[-0.00043354612363482806, -0.00043354612363482806, -0.0005256680055141886]]]
epoch over
tempforwardpass is
[0.9768279733521185]
tempforwardpass is
[0.9767429043056928]
tempforwardpass is
[0.04248446124149183]
tempforwardpass is
[0.9955030411840243]
cost is
0.00036287342558458737
numiter is
7938
numwholedata pass is
1984
ioindex is 1
simulated deljtheata
[[[-0.00037609056201855267, 0.0, -0.00037609056201855267], [-

In [5]:
pow(10,-3)

0.001